## New Chimes Plots Module How-to Guide
The new CHIMES plots module is a reworking of the previous plots code to provide better code organization, tests, and leverage the newer `plotly` module to draw figures rather than the old `matplotlib`. The module provides a consistent interface and means of working with each plot type, and the provided classes can be extended to tweak or create new figures.

Conceptually, plots are pre-defined templates that translate the results and variables from a given CHIMES hub into a figure or set of figures for visualization. The basic workflow when using plots is:
1. Use the CHIMES hub to instantiate and run a model
2. Create a plot object via one of the classes
3. Use `plot.load_variables(hub)` to load results into the plot
4. Use `plot.generate()` to build figures with the results
5. Use `plot.show()` to display the resulting figure, generally in a browser 

The code is located under `chimes/plots`, with the plots broken out into separate files. `filter.py` contains filters which can be used to select and modify which model variables will make it to the figures. `plot.py` contains the most basic plot definitions, though note these are meant to be abstract classes and are incomplete base definitions. The remaining files (`plotbyunits.py`, `showsensitivity.py`, `xy.py`, etc) are complete plot definitions that inherit from the base plots.

The following examples illustrate how to work with the module.

## Import

In [1]:
import os
import sys

sys.path.insert(0, '../../../')

import chimes as chm
from chimes.plots.plot import Plot
from chimes..filter import FilterType, Filter, KeyFilter, UnitFilter
from chimes.plots.showsensitivity import ShowSensitivity
from chimes.plots.plotbyunits import PlotByUnits
# ...


## Running a model
Before we can plot anything we need to run a model and generate some results. We'll run a basic GK model below that will be used in each example plot.

In [14]:
hub = chm.Hub('GK') # Load the model called 'GK'

# # Instantiate a GK model and setup initial params & preset
hub.set_dfields('Delta', 0.01)
hub.set_dfields('Tsim', 5)
hub.set_dfields('dt', 0.1)

# # Run the simulation and generate figures
OUT = hub.run_sensitivity(verb=False, std=0.05)

The following fields are defined in the model but not it the library :
The following fields are identified as parameters :
	- independant : ['alpha', 'n', 'delta', 'r', 'nu', 'eta', 'mu', 'k0', 'k1', 'k2', 'phinull']
	- function of other parameters : ['phi0', 'phi1']
The following variables are identified as auxilliary :
	 - differential : ['Dh', 'time']
	 - state variable : ['d', 'g', 'GDP']
The following order has been determined for functions:
	- parameter: ['nt', 'phi0', 'phi1']
	- statevar: ['Y', 'L', 'GDP', 'd', 'omega', 'employment', 'c', 'Pi', 'inflation', 'phillips', 'pi', 'kappa', 'I', 'Ir', 'g', 'C']
	- differential: ['a', 'N', 'K', 'w', 'p', 'D', 'Dh', 'time']

Changing Fields: ['Delta']

Changing Dimensions: ['Tsim']

Changes Ignored:['dt']

Changing Dimensions: ['nx']
Changing Fields: ['a', 'N', 'K', 'w', 'p', 'D', 'Dh', 'Delta', 'alpha', 'n', 'delta', 'r', 'nu', 'eta', 'mu', 'k0', 'k1', 'k2', 'phinull']
Now nx has 10 sectors with names [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]


### Filtering for specific variables
The `Filter` class defines a basic variable filter. Its constructor takes 
1. `include` - Boolean `True` or `False` which controls whether the filter will include or exclude target variables
2. `type` - Specifies which variables are targeted by the filter. Ex: `KEY` targets individual variables by name, while `UNIT` targets all variables in the given unit. Uses the `FilterType` enum defined in the same file
3. `field` - Filter target

There are also a number of subclasses that act as shorthands for common combinations. For example, `IncludeKeyFilter` sets `include=True` and `type=FilterType.KEY` by default, which `ExcludeKeyFilter` sets `include=False`

By default when there are no filters all variables are copied over. If there are any include filters, they are run first to produce the base set of variables. Once that has been established, any remaining exclude filters are run to produce the file variable set.

## ShowSensitivity
### Display sensitivity of all variables 

In [24]:
from chimes.plots.showsensitivity import ShowSensitivity

sensitivity = ShowSensitivity()

# By default if there are no filters all variables will be loaded
sensitivity.load_variables(OUT)

sensitivity.generate('employment')
sensitivity.show()

In [5]:
# Show sensitivity for only delta

from chimes..filter import IncludeKeyFilter

sensitivity = ShowSensitivity()

sensitivity.set_filters([IncludeKeyFilter(field='delta')])
# OR using a basic filter: 
# sensitivity.set_filters([Filter(include=True, type=FilterType.KEY, field='delta)])

sensitivity.load_variables(OUT)

sensitivity.generate('employment')
sensitivity.show()

In [25]:
# Show sensitivity for multiple explicitly defined fields

from chimes..plots.tools.filter import IncludeKeyFilter

sensitivity = ShowSensitivity()

sensitivity.set_filters([
    IncludeKeyFilter(field='_COMBINED_'),
    IncludeKeyFilter(field='delta'),
    IncludeKeyFilter(field='K')    
])

sensitivity.load_variables(OUT)

sensitivity.generate('omega')
sensitivity.show()

In [17]:
# Show sensitivity for everything except delta

from chimes..plots.tools.filter import ExcludeKeyFilter

sensitivity = ShowSensitivity()

sensitivity.set_filters([ExcludeKeyFilter(field='delta')])
# OR using a basic filter: 
# sensitivity.set_filters([Filter(include=False, type=FilterType.KEY, field='delta)])

sensitivity.load_variables(OUT)

sensitivity.generate('d')
sensitivity.show()

In [18]:
# Exclude filters take precedence over includes, therefore if you exclude a variable it will never appear 
# in the plot even if there is an include filter in the filter list

from chimes..plots.tools.filter import IncludeKeyFilter, ExcludeKeyFilter

sensitivity = ShowSensitivity()

sensitivity.set_filters([
    IncludeKeyFilter(field='_COMBINED_'),
    IncludeKeyFilter(field='delta'),
    IncludeKeyFilter(field='K'),
    ExcludeKeyFilter(field='delta') # Excluding delta here overrides the include above, plot will only contain _COMBINED_ and K
])

sensitivity.load_variables(OUT)

sensitivity.generate('employment')
sensitivity.show()

In [ ]:
# Show sensitivity for all variables with unit $

from chimes..plots.tools.filter import IncludeUnitFilter

sensitivity = ShowSensitivity()

sensitivity.set_filters([IncludeUnitFilter(field='')])

sensitivity.load_variables(OUT)

sensitivity.generate('employment')
sensitivity.show()

## PlotByUnits

In [1]:
hub = chm.Hub('GK')
hub.run()
from chimes.plots.plotbyunits import PlotByUnits

plot = PlotByUnits()
plot.load_variables(hub)
plot.set_filters([
    IncludeUnitFilter(field=['','$','Humans']),
    #IncludeUnitFilter(field='$'),
    #IncludeUnitFilter(field='Humans')
])

plot.generate()
plot.show()

NameError: name 'chm' is not defined

In [21]:
# Show all traces for all variables



In [22]:
# Show traces for specific units

from chimes.plots.plotbyunits import PlotByUnits
from chimes..plots.tools.filter import IncludeUnitFilter

plot = PlotByUnits()

plot.set_filters([
    IncludeUnitFilter(field=['','$','Humans']),
    #IncludeUnitFilter(field='$'),
    #IncludeUnitFilter(field='Humans')
])

plot.load_variables(hub)

plot.generate()
plot.show()

In [23]:
# Exclude traces for specific variables

from chimes.plots.plotbyunits import PlotByUnits
from chimes..plots.tools.filter import ExcludeUnitFilter

plot = PlotByUnits()

plot.set_filters([
    ExcludeUnitFilter(field=''),
    ExcludeUnitFilter(field='$'),
    ExcludeUnitFilter(field='Humans')
])

plot.load_variables(hub)

plot.generate()
plot.show()